# Documentation

Title:
Dual LoRA Fine-Tuned LLM for Patient Monitoring System

**********************************************

Introduction

This project focuses on the efficient fine-tuning and deployment of a large language model (LLM) using LoRA/QLoRA adapters on an edge AI device. LLM can be hosted on edge device or can be offered as a cloud service with high optimisation. The system adapts a shared base LLM for 3 distinct but complementary healthcare applications, using low-rank adaptation to minimize resource demands while preserving performance.

**********************************************
Key Features

Shared Base LLM with LoRA Adapters:
- Uses a single quantized LLM backbone (4-bit).
- Deploys two task-specific LoRA/QLoRA adapters in .safetensors format.
- Enables modular loading depending on the active task, conserving memory.

Edge-Optimized Inference:
- Runs locally on Jetson Orin Nano, ensuring low-latency and offline capabilities.
- Optimized via quantization, 4-bit loading (bitsandbytes), and selective adapter loading.

Natural Language Interfaces:
- Accepts unstructured inputs via speech or text.
- Can interface with a voice front-end or mobile app for broader accessibility.

**********************************************
Technical Highlights
- LoRA/QLoRA Fine-tuning Pipeline:
Base model: LLaMA2-7B (4-bit) or similar lightweight LLM.
Task 1 adapter fine-tuned on medical symptom → condition mappings.
Task 2 adapter trained on health education data (clinical + layman terms).
Task 3 adapter trained to provide diet plan.

- Training via HuggingFace Trainer + PEFT, quantisation with memory-efficient strategies.

- Deployment with SafeTensor Adapters:
Both adapters saved in .safetensors for secure, portable inference.
Adapters are dynamically loadable on-device via PEFT.

- Memory Efficiency:
4-bit base model reduces memory by ~75%.

**********************************************
Novelty:
- LLM deployment for dual healthcare NLP tasks on an embedded device.
- Enables multi-task inference with just adapter switching — memory optimised ideal for resource-constrained settings.
- Demonstrates that LoRA + QLoRA adapters can be strategically used for modular AI on edge.
**********************************************

Core Idea:

Since the output fine-tuned model is saved as safetensors and adaptors over the base model, we can have multiple fine-tuned safetensors cum adapters accessing the same base model minimising the memory required for edge deployment.

So, we are fine-tuning one LLM model for 2 applications with 2 datasets (diagnostic agent and diet recommendation) and storing the output fine-tuned model as safetensors, adaptors.


******************************************


Overview of the Fine-Tuning Pipeline

1.1 Dataset Preparation:

1.1.1 Diagnostic agent -

- Source: FreedomIntelligence/medical-o1-reasoning-SFT
- Combines the prompt and response into a given template to train the LLM on these prompt-response pairs
- Final format = "prompt" + "response" stored under 'text' column of the dataframe, for supervised instruction tuning.

1.1.2 Health Edu Gen + One-day diet planner:

- Source: issai/LLM_for_Dietary_Recommendation_System
- Contains 11.6k rows with 50 patient data split across several cells irregularly. So, pre-processed the dataset into a customised dataframe of shape 50 x 3 [50 patients ecah having 3 columns - Patient Profile (medical history), Health Education Generation, One-day diet plan]
- Thus the dataset was cleaned into a structured df and furthur arranged by combining the prompt and response into a given template to train the LLM on these prompt-response pairs

1.2 Template for LLM Supervised Fine-tuning

1.2.1 Diagnostic:
```
Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Given the patient's health symptoms generate the diagnosis based on the patient health : ...
Given this clinical presentation and history, what is the most likely diagnosis?

### Response:

```

Example:
```
<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis?


### Response:
The most likely diagnosis for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy.
### End<｜end▁of▁sentence｜>
```


1.2.2 Health Edu Gen:

Below is an instruction that describes a task. Write a response that appropriately completes the request.

```
### Instruction:
You are a health and diet tips generator.
Provide dietary recommendation for this patient profile:

### Response:

```

1.2.3 One-day Diet Plan:
```
Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a diet tips generator.
Given this patient profile: ...
Give a specific diet plan for the day (one-day diet plan) based on the patient profile using Central Asian food.

### Response:

```



1.3 Model & Tokenizer Loading: (same for all 3)

- Model: deepseek-ai/DeepSeek-R1-Distill-Llama-8B
- Loading with:

  - 4-bit quantization (QLoRA) using bitsandbytes
  - device_map="auto" for memory-aware loading across GPUs (it helps avoid overflow)
  - Tokenizer and model both loaded with a HuggingFace access token for private model access.


1.4 LoRA Adapter Setup: (same for all 3)

- prepare_model_for_kbit_training(model): enables gradient checkpointing and unfreezes input layers

- get_peft_model(...): attaches LoRA adapters for fine-tuning only a small subset of parameters

- print_trainable_parameters(): confirms minimal layers are trainable Here,
```
trainable params: 44,060,672 || all params: 8,074,321,920 || trainable%: 0.5457
```


1.5 Training with SFTTrainer (from trl): (same for all 3)

- Very lightweight: only 1000 samples
- Hyperparameters: small batch size, gradient accumulation, short steps, 8-bit optimizer, weight decay
- Output: a LoRA adapter file (.safetensors) containing only the fine-tuned weights, not the full model


**********************************************


Concepts Used

* LoRA (Low-Rank Adaptation) -	Fine-tunes only a few extra trainable matrices inserted into attention layers. Keeps base model frozen.
* QLoRA - 	Uses 4-bit quantization for the base model to reduce memory. Combined with LoRA to enable fine-tuning.
* BitsAndBytes Quantization	- Allows model weights to be loaded in 8-bit or 4-bit precision to save memory.
* PEFT (Parameter Efficient Fine-Tuning)	- Framework to plug in LoRA or other adapter methods into existing HF Transformers easily.
* SFT (Supervised Fine-Tuning)	- Standard fine-tuning where the model learns from input-output examples using full supervision.
* Gradient Accumulation -	Helps simulate larger batch sizes without exceeding memory limits.


**********************************************


How Optimized is This Setup?

1. Efficient memory usage: 4-bit quantized base model fits even on edge AI device with 8-16 GB RAM.

2. LoRA adapter training avoids full weight updates → reduces memory, compute, and saves energy.

3. Fast and Lightweight Training: Only fine-tuning adapter weights (~1-2% of model size). Uses 8-bit optimizer (adamw_8bit) and short training schedule for quick iteration.

# Imports

In [ ]:
! pip install -U transformers peft trl accelerate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 411.1/411.1 kB 13.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 336.4/336.4 kB 28.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 354.7/354.7 kB 33.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 41.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 75.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 70.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 50.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 19.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
! pip install transformers datasets peft bitsandbytes accelerate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.1/76.1 MB 8.5 MB/s eta 0:00:00


In [ ]:
!pip install compressed-tensors

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.4/98.4 kB 3.2 MB/s eta 0:00:00


In [ ]:
!pip install -q -U bitsandbytes
!pip install -q -U transformers
!pip install -q -U accelerate

In [ ]:
! python -m bitsandbytes

++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
++++++++++++++++++ BUG REPORT INFORMATION ++++++++++++++++++
++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
++++++++++++++++++++++++++ OTHER +++++++++++++++++++++++++++
CUDA specs: CUDASpecs(highest_compute_capability=(7, 5), cuda_version_string='124', cuda_version_tuple=(12, 4))
PyTorch settings found: CUDA_VERSION=124, Highest Compute Capability: (7, 5).
To manually override the PyTorch CUDA version please see: https://github.com/TimDettmers/bitsandbytes/blob/main/docs/source/nonpytorchcuda.mdx
The directory listed in your path is found to be non-existent: /sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events
The directory listed in your path is found to be non-existent: //172.28.0.1
The directory listed in your path is found to be non-existent: 8013
The directory listed in your path is found to be non-existent: //colab.research.google.com/tun/m/cc48301118ce562b961b3c22d803539adc1e0c19/

In [ ]:
hugging_face_token = ''

# 1. 8B Model for Diagnostic Agent

## Fine-tuning diagnostic agent

In [ ]:
# Modules for fine-tuning
import torch # Import PyTorch
from trl import SFTTrainer # Trainer for supervised fine-tuning (SFT)
# from unsloth import is_bfloat16_supported # Checks if the hardware supports bfloat16 precision
# Hugging Face modules
from huggingface_hub import login # Lets you login to API
from transformers import TrainingArguments # Defines training hyperparameters
from datasets import load_dataset # Lets you load fine-tuning datasets

import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

In [ ]:
import pandas as pd
from datasets import load_dataset
from datasets import Dataset

#Load the dataset from the HuggingFace Hub
rd_ds = load_dataset("FreedomIntelligence/medical-o1-reasoning-SFT", 'en')

#Convert to pandas dataframe for convenient processing
rd_df = pd.DataFrame(rd_ds['train'])

#Combine the two attributes into an instruction string
rd_df['instruction'] = "Given the patient's health symptoms generate the diagnosis based on the patient health : " + rd_df['Question']

rd_df = rd_df[['instruction', 'Complex_CoT', 'Response']]

#Get a 1000 sample subset for fine-tuning purposes
rd_df_sample = rd_df.sample(n=1000, random_state=42)

#Define template and format data into the template for supervised fine-tuning
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:

{}

### Response:\n"""

rd_df_sample['prompt'] = rd_df_sample["instruction"].apply(lambda x: template.format(x))
rd_df_sample.rename(columns={'Response': 'response'}, inplace=True)
rd_df_sample['response'] = rd_df_sample['response'] + "\n### End"
rd_df_sample = rd_df_sample[['prompt', 'response']]

rd_df_sample['text'] = rd_df_sample["prompt"] + rd_df_sample["response"]
rd_df_sample.drop(columns=['prompt', 'response'], inplace=True)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/1.65k [00:00<?, ?B/s]

medical_o1_sft.json:   0%|          | 0.00/74.1M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/25371 [00:00<?, ? examples/s]

In [ ]:
rd_df_sample

text
6460   Below is an instruction that describes a task....
18018  Below is an instruction that describes a task....
16564  Below is an instruction that describes a task....
15409  Below is an instruction that describes a task....
6798   Below is an instruction that describes a task....
...                                                  ...
7567   Below is an instruction that describes a task....
24345  Below is an instruction that describes a task....
9188   Below is an instruction that describes a task....
3393   Below is an instruction that describes a task....
3265   Below is an instruction that describes a task....

[500 rows x 1 columns]

In [ ]:
rd_ds

DatasetDict({
    train: Dataset({
        features: ['Question', 'Complex_CoT', 'Response'],
        num_rows: 25371
    })
})

In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"

model_path = 'deepseek-ai/DeepSeek-R1-Distill-Llama-8B'

tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)

#Pass in a prompt and infer with the model
prompt = "Q: Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? \nA:"
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=128
)

print(tokenizer.decode(generation_output[0]))

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/usr/local/lib/python3.11/dist-packages/bitsandbytes/nn/modules.py:451: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(


<｜begin▁of▁sentence｜>Q: Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? 
A: Multiple Sclerosis (MS)
B: Alzheimer's Disease
C: Posterior fossa tumor
D: Cerebral Infarction
Okay, so I have this medical case to think through. A 45-year-old man with a history of alcohol use, now abstinent for 10 years. He's presenting with sudden onset dysarthria, shuffling gait, and intention tremors. I need to figure out what his diagnosis is most likely. The options are MS, Alzheimer's, posterior fossa tumor, or cerebral infarction.

First, let me break down each symptom and what they could indicate.

D


In [ ]:
from peft import LoraConfig

#If only targeting attention blocks of the model
target_modules = ["q_proj", "v_proj"]

#If targeting all linear layers
target_modules = ['q_proj','k_proj','v_proj','o_proj','gate_proj','down_proj','up_proj','lm_head']

lora_config = LoraConfig(
r=16,
target_modules = target_modules,
lora_alpha=8,
lora_dropout=0.05,
bias="none",
task_type="CAUSAL_LM"
)

In [ ]:
import re
model_modules = str(model.modules)
pattern = r'\((\w+)\): Linear'
linear_layer_names = re.findall(pattern, model_modules)

names = []
# Print the names of the Linear layers
for name in linear_layer_names:
    names.append(name)
target_modules = list(set(names))

In [ ]:
target_modules

['lm_head',
 'o_proj',
 'gate_proj',
 'up_proj',
 'v_proj',
 'down_proj',
 'k_proj',
 'q_proj']

In [ ]:
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training

# Define training arguments
training_args=TrainingArguments(
    per_device_train_batch_size=2,  # Number of examples processed per device (GPU) at a time
    gradient_accumulation_steps=4,  # Accumulate gradients over 4 steps before updating weights
    num_train_epochs=1, # Full fine-tuning run
    warmup_steps=5,  # Gradually increases learning rate for the first 5 steps
    max_steps=60,  # Limits training to 60 steps (useful for debugging; increase for full fine-tuning)
    learning_rate=2e-4,  # Learning rate for weight updates (tuned for LoRA fine-tuning)
    logging_steps=10,  # Logs training progress every 10 steps
    optim="adamw_8bit",  # Uses memory-efficient AdamW optimizer in 8-bit mode
    weight_decay=0.01,  # Regularization to prevent overfitting
    lr_scheduler_type="linear",  # Uses a linear learning rate schedule
    seed=3407,  # Sets a fixed seed for reproducibility
    output_dir="outputs",  # Directory where fine-tuned model checkpoints will be saved
)


dataset = Dataset.from_pandas(rd_df_sample)
dataset_dict = DatasetDict({"train": dataset})


# Prepare for training by enabling input gradients and such
model = prepare_model_for_kbit_training(model)

# Attach LoRA adapters
model = get_peft_model(model, lora_config)
model.print_trainable_parameters()  # Optional: shows which params will be trained

trainer = SFTTrainer(
  model=model,
  train_dataset=dataset_dict["train"],  # Dataset used for training
  args=training_args,
)

# Initiate the training process
with mlflow.start_run(run_name= 'run_name_of_choice'):
  trainer.train()

trainable params: 44,060,672 || all params: 8,074,321,920 || trainable%: 0.5457


Converting train dataset to ChatML:   0%|          | 0/1000 [00:00<?, ? examples/s]

Applying chat template to train dataset:   0%|          | 0/1000 [00:00<?, ? examples/s]

Tokenizing train dataset:   0%|          | 0/1000 [00:00<?, ? examples/s]

Truncating train dataset:   0%|          | 0/1000 [00:00<?, ? examples/s]

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


NameError: name 'mlflow' is not defined

In [ ]:
# Start the fine-tuning process
trainer_stats = trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: nithya-3169 (nithya-3169-r-v-c-e) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


In [ ]:
# Start the fine-tuning process
trainer_stats = trainer.train()

In [ ]:
#Pass in a prompt and infer with the model
prompt = "Q: Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? \nA:"
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=128
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


<｜begin▁of▁sentence｜>Q: Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? 
A: Wilson's disease
B: Huntington's disease
C: Spinocerebellar ataxia
D: Posterior fossa tumors
E: Multiple sclerosis
F: Alcoholic cerebellar degeneration
G: Cerebral amyloidosis
H: Progressive supranuclear palsy (PSP)
I: Alzheimer's disease
J: Idiopathic parkinsonsonism
K: Acute disseminated encephalomyelitis (ADEM)
L: Spinal cord compression
M: Cerebral infarction
N: Neurocysticercosis
O: Acute alcohol withdrawal


In [ ]:
instruction = "Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? \n"
prompt = template.format(instruction)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=128
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:

Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? 


### Response:
The most likely diagnosis for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numb

In [ ]:
model_name = "model_ft_diagnostic"

# Save the fine-tuned model
model.save_pretrained(model_name)

# Save the tokenizer
tokenizer.save_pretrained(model_name)


('model_ft_diagnostic/tokenizer_config.json',
 'model_ft_diagnostic/special_tokens_map.json',
 'model_ft_diagnostic/tokenizer.json')

In [ ]:
from google.colab import files
import shutil

# Define the source directory of the model
model_dir = "outputs"

# Create a zip archive of the model directory
shutil.make_archive(model_dir, 'zip', model_dir)

# Download the zip file
files.download(f'{model_dir}.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from google.colab import files
import shutil

# Define the source directory of the model
model_dir = "model_ft_diagnostic"

# Create a zip archive of the model directory
shutil.make_archive(model_dir, 'zip', model_dir)

# Download the zip file
files.download(f'{model_dir}.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Inference

In [ ]:
# transformers                          4.51.3
# peft                                  0.15.2
# accelerate                            1.6.0
# bitsandbytes                          0.45.5
# datasets                              3.5.0

# triton                                3.2.0
# trl                                   0.16.1
# tensorflow                            2.18.0
# torch                                 2.6.0+cu124
# wandb                                 0.19.9
# safetensors                           0.5.3
# scikit-learn                          1.6.1
# nvidia-cuda-nvcc-cu12                 12.5.82

In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"
model_path = 'deepseek-ai/DeepSeek-R1-Distill-Llama-8B'
tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)


The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel, PeftConfig

# Load the adapter config to find the base model
peft_model_path = "model_ft_diagnostic"
config = PeftConfig.from_pretrained(peft_model_path)

# Load the model with the LoRA adapters
model = PeftModel.from_pretrained(model, peft_model_path)

# Set to eval mode
model.eval()


PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(128256, 4096)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
              (k_proj): lor

In [ ]:
#Define template and format data into the template for supervised fine-tuning
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:

{}

### Response:\n"""

instruction = "Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? \n"
prompt = template.format(instruction)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=128, temperature=0.7,
    top_p=0.95
)

print(tokenizer.decode(generation_output[0], skip_special_tokens=True))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/usr/local/lib/python3.11/dist-packages/bitsandbytes/nn/modules.py:451: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(


Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:

Given the patient's health symptoms generate the diagnosis based on the patient health : A 45-year-old man with a history of alcohol use, who has been abstinent for the past 10 years, presents with sudden onset dysarthria, shuffling gait, and intention tremors. Given this clinical presentation and history, what is the most likely diagnosis? 


### Response:
Based on the patient's clinical presentation and history, the most likely diagnosis is cerebellar dysfunction. This is particularly concerning given his history of alcohol use, as prolonged alcohol use can lead to chronic liver disease, which may cause issues in the brain such as Wernicke-Korsakoff syndrome. This syndrome involves damage to the cerebellum, which can manifest as dysarthria, shuffling gait, and intention tremors. Therefore, it is reasonable to suspect that the patient's cerebellar dysfunction is

# 2. 8B Model for Diet Tips [Together]

## Dataset Preperation

In [ ]:
# Modules for fine-tuning
import torch # Import PyTorch
from trl import SFTTrainer # Trainer for supervised fine-tuning (SFT)
# from unsloth import is_bfloat16_supported # Checks if the hardware supports bfloat16 precision
# Hugging Face modules
from huggingface_hub import login # Lets you login to API
from transformers import TrainingArguments # Defines training hyperparameters
from datasets import load_dataset # Lets you load fine-tuning datasets
import pandas as pd
from datasets import Dataset
import pandas as pd
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

In [ ]:
import pandas as pd
from datasets import load_dataset
from datasets import Dataset

#Load the dataset from the HuggingFace Hub
diet_ds = load_dataset("issai/LLM_for_Dietary_Recommendation_System")


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/4.70k [00:00<?, ?B/s]

cases_results.zip:   0%|          | 0.00/131k [00:00<?, ?B/s]

cases_results_1.zip:   0%|          | 0.00/158k [00:00<?, ?B/s]

cases_results_1_tr.zip:   0%|          | 0.00/191k [00:00<?, ?B/s]

cases_results_2.zip:   0%|          | 0.00/159k [00:00<?, ?B/s]

cases_results_2_tr.zip:   0%|          | 0.00/182k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/11634 [00:00<?, ? examples/s]

In [ ]:
diet_ds

DatasetDict({
    train: Dataset({
        features: ['text'],
        num_rows: 11634
    })
})

In [ ]:
whole_text = ""
whole_text = [whole_text + " " + row["text"] for row in diet_ds['train']]
whole_text = "".join(whole_text)

In [ ]:
whole_text

' Provide dietary recommendation for this patient profile.  Young Model Staying in Shape Name: Amina Gender: Female Age: 22 Nationality: Kazakhstani Location: Almaty, Kazakhstan Family Information: Marital Status: Single Family Members: Mother, Father, one younger brother Occupation: Amina: Professional model Mother: Homemaker Father: Business owner  Cultural Background: Amina and her family follow the religion of Islam and do not consume pork in their diet. They primarily consume Kazakh traditional food with influences from Central Asian and Russian dishes. They occasionally enjoy international cuisine in Almaty\'s diverse food scene.  Lifestyle Information: Amina has an active lifestyle, participating in fashion shows, photo shoots, and model castings. She engages in regular exercise, including yoga, running, and strength training to stay in shape and maintain her fitness.  Diet History: Breakfast: Smoothie with almond milk, banana, spinach, and protein powder or overnight oats with 

In [ ]:
! pip install deep-translator

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.3/42.3 kB 2.3 MB/s eta 0:00:00


In [ ]:
from deep_translator import GoogleTranslator
from tqdm import tqdm

# Your input text (replace this with your actual text)
text = whole_text

# Optional: clean up extra spaces
text = re.sub(r'\s+', ' ', text).strip()

# Break into chunks for translation (safely under token limit)
chunks = textwrap.wrap(text, width=500, break_long_words=False, replace_whitespace=False)

translated_chunks = []
for i, chunk in tqdm(enumerate(chunks)):
    try:
        translated = GoogleTranslator(source='auto', target='en').translate(chunk)
        translated_chunks.append(translated)
    except Exception as e:
        print(f"Translation error in chunk {i}: {e}")
        translated_chunks.append(chunk)  # fallback

# Rejoin translated chunks
translated_text = ' '.join(translated_chunks)

# Normalize case
translated_text_lower = translated_text.lower()

2741it [43:05,  1.06it/s]


In [ ]:
translated_text_lower

'provide dietary recommendation for this patient profile. young model staying in shape name: amina gender: female age: 22 nationality: kazakhstani location: almaty, kazakhstan family information: marital status: single family members: mother, father, one younger brother occupation: amina: professional model mother: homemaker father: business owner cultural background: amina and her family follow the religion of islam and do not consume pork in their diet. they primarily consume kazakh traditional food with influences from central asian and russian dishes. they occasionally enjoy international cuisine in almaty\'s diverse food scene. lifestyle information: amina has an active lifestyle, participating in fashion shows, photo shoots, and model castings. she engages in regular exercise, including yoga, running, and strength training to stay in shape and maintain her fitness. diet history: breakfast: smoothie with almond milk, banana, spinach, and protein powder or overnight oats with fruit

In [ ]:
with open("translated_text_lower.txt", "w", encoding="utf-8") as file:
    file.write(translated_text_lower)

In [ ]:
import re
import pandas as pd

# Your large text blob
text = whole_text

# Define markers
prof_marker = "provide dietary recommendation for this patient profile"
# prof_marker_2 = "provide a meal for the ot patient \/ patient profile"
rec_marker = "dietary recommendations"
rec_marker_2 = "recommendations for"
plan_marker = "give a specific diet plan for the day based on the patient profile using central asian food"

# Normalize the text for easier pattern matching (case insensitive)
text_lower = text.lower()

# Split based on the recommendation marker
# split_data = re.split(f"(?=({prof_marker}|{prof_marker_2}))", text_lower)
split_data = re.split(f"(?=({prof_marker}))", text_lower)

# Clean out any accidental empty entries
split_data = [entry.strip() for entry in split_data if entry.strip()]

# Process each chunk to get the recommendation and plan parts
data_rows = []

for chunk in split_data:
    if prof_marker or prof_marker_2 in chunk:

        if rec_marker in chunk:
            prof_part, plan_part = chunk.split(rec_marker, 1)
            prof_part = prof_part.strip()
            plan_part = rec_marker + plan_part.strip()  # add the marker back
        elif rec_marker_2 in chunk:
            prof_part, plan_part = chunk.split(rec_marker_2, 1)
            prof_part = prof_part.strip()
            plan_part = rec_marker_2 + plan_part.strip()  # add the marker back
        else:
            prof_part = chunk.strip()
            plan_part = ""  # no diet plan provided yet

        # Try to split at the plan marker
        if plan_marker in plan_part:
            rec_part, plan_part = plan_part.split(plan_marker, 1)
            rec_part = rec_part.strip()
            plan_part = plan_marker + plan_part.strip()  # add the marker back
        else:
            rec_part = plan_part.strip()
            plan_part = ""  # no diet plan provided yet
        data_rows.append([prof_part, rec_part, plan_part])

# Convert to DataFrame
df = pd.DataFrame(data_rows, columns=["PatientProfile", "Recommendation", "DietPlan"])

# Show the result
print(df.head())


                                      PatientProfile  \
0  provide dietary recommendation for this patien...   
1  provide dietary recommendation for this patien...   
2  provide dietary recommendation for this patien...   
3  provide dietary recommendation for this patien...   
4  provide dietary recommendation for this patien...   

                                      Recommendation  \
0                                                      
1  dietary recommendations:  1. increase calorie ...   
2                                                      
3  dietary recommendations:  1. increase intake o...   
4                                                      

                                            DietPlan  
0                                                     
1  give a specific diet plan for the day based on...  
2                                                     
3  give a specific diet plan for the day based on...  
4                                                  

In [ ]:
# remove rows with null values in any one column in df

df = df.dropna()

In [ ]:
df.shape

(100, 3)

In [ ]:
df

PatientProfile  \
0   provide dietary recommendation for this patien...   
1   provide dietary recommendation for this patien...   
2   provide dietary recommendation for this patien...   
3   provide dietary recommendation for this patien...   
4   provide dietary recommendation for this patien...   
..                                                ...   
95  provide dietary recommendation for this patien...   
96  provide dietary recommendation for this patien...   
97  provide dietary recommendation for this patien...   
98  provide dietary recommendation for this patien...   
99  provide dietary recommendation for this patien...   

                                       Recommendation  \
0                                                       
1   dietary recommendations:  1. increase calorie ...   
2                                                       
3   dietary recommendations:  1. increase intake o...   
4                                                       
..                                                ...   
95  dietary recommendations:  1. breakfast: opt fo...   
96                                                      
97  dietary recommendations:  1. maintain a well-b...   
98                                                      
99  dietary recommendations:  1. carbohydrates: as...   

                                             DietPlan  
0                                                      
1   give a specific diet plan for the day based on...  
2                                                      
3   give a specific diet plan for the day based on...  
4                                                      
..                                                ...  
95  give a specific diet plan for the day based on...  
96                                                     
97  give a specific diet plan for the day based on...  
98                                                     
99  give a specific diet plan for the day based on...  

[100 rows x 3 columns]

In [ ]:
# prompt: delete all even number rows from df... 0,2,4 ... upto 100. and all rows >= 102

# Delete even-numbered rows up to 100 and rows >= 102
rows_to_delete = list(range(0, 99, 2))
df_new = df.drop(index=rows_to_delete)


In [ ]:
df_new.shape

(50, 3)

In [ ]:
df_new

PatientProfile  \
1   provide dietary recommendation for this patien...   
3   provide dietary recommendation for this patien...   
5   provide dietary recommendation for this patien...   
7   provide dietary recommendation for this patien...   
9   provide dietary recommendation for this patien...   
11  provide dietary recommendation for this patien...   
13  provide dietary recommendation for this patien...   
15  provide dietary recommendation for this patien...   
17  provide dietary recommendation for this patien...   
19  provide dietary recommendation for this patien...   
21  provide dietary recommendation for this patien...   
23  provide dietary recommendation for this patien...   
25  provide dietary recommendation for this patien...   
27  provide dietary recommendation for this patien...   
29  provide dietary recommendation for this patien...   
31  provide dietary recommendation for this patien...   
33  provide dietary recommendation for this patien...   
35  provide dietary recommendation for this patien...   
37  provide dietary recommendation for this patien...   
39  provide dietary recommendation for this patien...   
41  provide dietary recommendation for this patien...   
43  provide dietary recommendation for this patien...   
45  provide dietary recommendation for this patien...   
47  provide dietary recommendation for this patien...   
49  provide dietary recommendation for this patien...   
51  provide dietary recommendation for this patien...   
53  provide dietary recommendation for this patien...   
55  provide dietary recommendation for this patien...   
57  provide dietary recommendation for this patien...   
59  provide dietary recommendation for this patien...   
61  provide dietary recommendation for this patien...   
63  provide dietary recommendation for this patien...   
65  provide dietary recommendation for this patien...   
67  provide dietary recommendation for this patien...   
69  provide dietary recommendation for this patien...   
71  provide dietary recommendation for this patien...   
73  provide dietary recommendation for this patien...   
75  provide dietary recommendation for this patien...   
77  provide dietary recommendation for this patien...   
79  provide dietary recommendation for this patien...   
81  provide dietary recommendation for this patien...   
83  provide dietary recommendation for this patien...   
85  provide dietary recommendation for this patien...   
87  provide dietary recommendation for this patien...   
89  provide dietary recommendation for this patien...   
91  provide dietary recommendation for this patien...   
93  provide dietary recommendation for this patien...   
95  provide dietary recommendation for this patien...   
97  provide dietary recommendation for this patien...   
99  provide dietary recommendation for this patien...   

                                       Recommendation  \
1   dietary recommendations:  1. increase calorie ...   
3   dietary recommendations:  1. increase intake o...   
5   dietary recommendationsfor aibek:  1. focus on...   
7   dietary recommendationsfor sabina:  1. consume...   
9   dietary recommendationsfor svetlana with iron ...   
11  dietary recommendationsfor erkinbek:  1. focus...   
13  dietary recommendationsfor li wei during her c...   
15  dietary recommendationsfor nursultan:  1. ener...   
17  dietary recommendationsfor mark:  1. emphasize...   
19  dietary recommendationsfor aida with chronic h...   
21  dietary recommendationsfor adelina:  1. balanc...   
23  dietary recommendationsfor shoakram:  1. conti...   
25  dietary recommendationsfor sevda:  given sevda...   
27  dietary recommendationsfor dilyara:  1. includ...   
29  dietary recommendationsfor aygul:  1. increase...   
31  dietary recommendationsfor lin khan:  1. base ...   
33                                                      
35  dietary recommendationsfor khan:  1. breakfast...   
37  dietary recommendationsare suggested to help

In [ ]:
df_new.to_csv("patient_profiles.csv", index=False)

## Fine-tuning

In [ ]:
diet_df = pd.read_csv("patient_profiles_final.csv", names=["PatientProfile", "Recommendation", "DietPlan"], header=0)

In [ ]:
diet_df.shape

(50, 3)

In [ ]:
# Step 1: Create a combined instruction string
diet_df['instruction'] = (
    "You are a health and diet tips generator. You need to provide the following 2 responses. \n\n" +
    "1. Provide dietary recommendation for this patient profile: " + diet_df['PatientProfile'].astype(str) + "\n\n" +
    "2. Give a specific diet plan for the day based on the patient profile using Central Asian food."
)

# Step 2: Combine both responses into a single response string
diet_df['response'] = (
    "1. Recommendation: " + diet_df['Recommendation'].astype(str) + "\n\n" +
    "2. One-day Diet Plan: " + diet_df['DietPlan']
)

# template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

# ### Instruction:
# You are a health and diet tips generator.
# 1. Provide dietary recommendation for this patient profile: {} \n
# 2. Give a specific diet plan for the day based on the patient profile using Central Asian food.

# ### Response:
# 1. Dietary recommendation: {} \n\n
# 2. One-day diet plan: {}


# ### End
# """

# Step 3: Define the prompt template
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}
"""

# Step 4: Apply template formatting
# diet_df['formatted_prompt'] = diet_df.apply(
#     lambda row: template.format(row['PatientProfile'], row['Recommendation'], row['DietPlan']),
#     axis=1
# )
diet_df['formatted_prompt'] = diet_df.apply(
    lambda row: template.format(row['instruction'], row['response']),
    axis=1
)

In [ ]:
diet_df.shape

(50, 4)

In [ ]:
print(diet_df['formatted_prompt'].iloc[5])


Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a health and diet tips generator. You need to provide the following 2 responses. 

1. Provide dietary recommendation for this patient profile:  recovery after long covid name: erkinbek age: 42 gender: male ethnicity: kyrgyz location: taraz, kazakhstan marital status: married, has 4 children occupation: welder medical history: long covid-19 recovery date of covid-19 diagnosis: 8 months ago symptoms: persistent fatigue, shortness of breath, brain fog, muscle weakness, loss of smell and taste current medication: none family history: has father with hypertension anthropometry and body composition: height: 175 cm weight: 83 kg bmi: 27.1 kg/m2 biochemical and hematological markers: blood pressure: 120/80 mmhg hemoglobin (hb): 13.5 g/dl white blood cells (wbc): 6,500 cells/mm³ platelet count: 200,000 cells/mm³ clinical: experienced severe respiratory symptoms dur

In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"

# model_path = 'LoftQ/Llama-2-7b-hf-4bit-64rank'
# model_path = 'TheBloke/Mistral-7B-Instruct-v0.1-GGUF'
# You cannot perform fine-tuning on purely quantized models. Please attach trainable adapters on top of the quantized model to correctly perform fine-tuning. Please see:
model_path = 'deepseek-ai/DeepSeek-R1-Distill-Llama-8B'
# tokenizer = LlamaTokenizer.from_pretrained(model_path)
# model = LlamaForCausalLM.from_pretrained(
# model_path, load_in_8bit=True, device_map='auto',
# ).to(device)
tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)



tokenizer_config.json:   0%|          | 0.00/3.07k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [ ]:
#Pass in a prompt and infer with the model
instruction = " folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. "

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
 folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors:

In [ ]:
import re
model_modules = str(model.modules)
pattern = r'\((\w+)\): Linear'
linear_layer_names = re.findall(pattern, model_modules)

names = []
# Print the names of the Linear layers
for name in linear_layer_names:
    names.append(name)
target_modules = list(set(names))

In [ ]:
target_modules

['lm_head',
 'q_proj',
 'k_proj',
 'v_proj',
 'o_proj',
 'down_proj',
 'gate_proj',
 'up_proj']

In [ ]:
from peft import LoraConfig

#If only targeting attention blocks of the model
target_modules = ["q_proj", "v_proj"]

#If targeting all linear layers
target_modules = ['q_proj','k_proj','v_proj','o_proj','gate_proj','down_proj','up_proj','lm_head']

lora_config = LoraConfig(
r=16,
target_modules = target_modules,
lora_alpha=8,
lora_dropout=0.05,
bias="none",
task_type="CAUSAL_LM"
)

In [ ]:
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training

# Define training arguments
training_args=TrainingArguments(
    per_device_train_batch_size=2,  # Number of examples processed per device (GPU) at a time
    gradient_accumulation_steps=4,  # Accumulate gradients over 4 steps before updating weights
    num_train_epochs=1, # Full fine-tuning run
    warmup_steps=5,  # Gradually increases learning rate for the first 5 steps
    max_steps=45,  # Limits training to 60 steps (useful for debugging; increase for full fine-tuning)
    learning_rate=2e-4,  # Learning rate for weight updates (tuned for LoRA fine-tuning)
    logging_steps=5,  # Logs training progress every 10 steps
    optim="adamw_8bit",  # Uses memory-efficient AdamW optimizer in 8-bit mode
    weight_decay=0.01,  # Regularization to prevent overfitting
    lr_scheduler_type="linear",  # Uses a linear learning rate schedule
    seed=3407,  # Sets a fixed seed for reproducibility
    output_dir="outputs",  # Directory where fine-tuned model checkpoints will be saved
)

# trainer = SFTTrainer(
#   model=model,
#   tokenizer=tokenizer,
#   train_dataset=rd_df_sample,  # Dataset used for training
#   dataset_text_field="text",  # Specifies which field in the dataset contains training text
#   max_seq_length=256,
#   dataset_num_proc=2,  # Uses 2 CPU threads to speed up data preprocessing
#   args=training_args,
# )

formatted_diet_df = diet_df[["formatted_prompt"]].copy()
formatted_diet_df = formatted_diet_df.rename(columns={"formatted_prompt": "text"})
dataset = Dataset.from_pandas(formatted_diet_df)
dataset_dict = DatasetDict({"train": dataset})


# Prepare for training by enabling input gradients and such
model = prepare_model_for_kbit_training(model)

# Attach LoRA adapters
model = get_peft_model(model, lora_config)
model.print_trainable_parameters()  # Optional: shows which params will be trained

trainer = SFTTrainer(
  model=model,
  train_dataset=dataset_dict["train"],  # Dataset used for training
  args=training_args,
)

# Initiate the training process
# with mlflow.start_run(run_name= 'run_name_of_choice'):
#   trainer.train()

trainable params: 44,060,672 || all params: 8,074,321,920 || trainable%: 0.5457


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Converting train dataset to ChatML:   0%|          | 0/50 [00:00<?, ? examples/s]

Applying chat template to train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

Tokenizing train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

Truncating train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [ ]:
# Start the fine-tuning process
trainer_stats = trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: mnithyashree-cs22 (chandanamn-cs23-na) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


In [ ]:
#Pass in a prompt and infer with the model
instruction = " folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. "

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
 folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors:

In [ ]:
#Pass in a prompt and infer with the model
instruction = " for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy "

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
 for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy 

### Response:

1. **Provide a clear diagnosis**: Based on the information provided, the most likely diagnosis is alcoholic neuropathy. This condition is commonly associated with chronic alcohol use and can lead to symptoms such as dysart

In [ ]:
model_name = "model_ft_diet"

# Save the fine-tuned model
model.save_pretrained(model_name)

# Save the tokenizer
tokenizer.save_pretrained(model_name)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


('model_ft_diet/tokenizer_config.json',
 'model_ft_diet/special_tokens_map.json',
 'model_ft_diet/tokenizer.json')

In [ ]:
from google.colab import files
import shutil

# Define the source directory of the model
model_dir = "model_ft_diet"

# Create a zip archive of the model directory
shutil.make_archive(model_dir, 'zip', model_dir)

# Download the zip file
files.download(f'{model_dir}.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Inference

In [ ]:
! unzip /content/model_ft_diet.zip

Archive:  /content/model_ft_diet.zip
  inflating: tokenizer_config.json   
  inflating: special_tokens_map.json  
  inflating: adapter_config.json     
  inflating: tokenizer.model         
  inflating: README.md               
  inflating: adapter_model.safetensors  
  inflating: tokenizer.json          


In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"
model_path = 'LoftQ/Llama-2-7b-hf-4bit-64rank'
tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)


The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.
/usr/local/lib/python3.11/dist-packages/transformers/quantizers/auto.py:212: UserWarning: You passed `quantization_config` or equivalent parameters to `from_pretrained` but the model you're loading already has a `quantization_config` attribute. The `quantization_config` from the model will be used.
  warnings.warn(warning_msg)


In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel, PeftConfig

# Load the adapter config to find the base model
peft_model_path = "model_ft_diet"
config = PeftConfig.from_pretrained(peft_model_path)

# # Load the base model
# base_model = AutoModelForCausalLM.from_pretrained(
#     config.base_model_name_or_path,
#     token=hugging_face_token,
#     load_in_4bit=True,
#     device_map="auto",  # or "cuda:0" if using GPU manually
# )

# # Load the tokenizer
# tokenizer = AutoTokenizer.from_pretrained(
#     config.base_model_name_or_path,
#     token=hugging_face_token,
#     load_in_4bit=True
# )

# Load the model with the LoRA adapters
model = PeftModel.from_pretrained(model, peft_model_path)

# Set to eval mode
model.eval()


PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(32000, 4096)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
              (k_proj): lora

In [ ]:
#Define template and format data into the template for supervised fine-tuning
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a health and diet tips generator.
1. Provide dietary recommendation for this patient profile: {} \n
2. Give a specific diet plan for the day based on the patient profile using Central Asian food.

### Response:
1. Dietary recommendation: {} \n\n
2. One-day diet plan: {}


### End
"""

#Pass in a prompt and infer with the model
instruction = " folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. "

prompt = template.format(instruction, "", "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=256
)

print(tokenizer.decode(generation_output[0], skip_special_tokens=True))

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a health and diet tips generator.
1. Provide dietary recommendation for this patient profile:  folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken,

# 3. Separation of models

## Dietary Recommendation Fine-tuning

### Fine-tuning

In [ ]:
# Modules for fine-tuning
import torch # Import PyTorch
from trl import SFTTrainer # Trainer for supervised fine-tuning (SFT)
# from unsloth import is_bfloat16_supported # Checks if the hardware supports bfloat16 precision
# Hugging Face modules
from huggingface_hub import login # Lets you login to API
from transformers import TrainingArguments # Defines training hyperparameters
from datasets import load_dataset # Lets you load fine-tuning datasets
import pandas as pd
from datasets import Dataset
import pandas as pd
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

In [ ]:
diet_df = pd.read_csv("patient_profiles_final.csv", names=["PatientProfile", "Recommendation", "DietPlan"], header=0)

In [ ]:
diet_df.shape

(50, 3)

In [ ]:
# Step 1: Create a combined instruction string
diet_df['instruction'] = (
    "You are a health and diet tips generator. \n\n" +
    "Provide dietary recommendation for this patient profile: " + diet_df['PatientProfile'].astype(str)
)

# Step 2: Combine both responses into a single response string
diet_df['response'] = (
    "Recommendation: " + diet_df['Recommendation'].astype(str) + "\n\n"
)

# Step 3: Define the prompt template
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}
"""

diet_df['formatted_prompt'] = diet_df.apply(
    lambda row: template.format(row['instruction'], row['response']),
    axis=1
)

In [ ]:
diet_df.shape

(50, 6)

In [ ]:
print(diet_df['formatted_prompt'].iloc[5])


Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a health and diet tips generator. 

Provide dietary recommendation for this patient profile:  recovery after long covid name: erkinbek age: 42 gender: male ethnicity: kyrgyz location: taraz, kazakhstan marital status: married, has 4 children occupation: welder medical history: long covid-19 recovery date of covid-19 diagnosis: 8 months ago symptoms: persistent fatigue, shortness of breath, brain fog, muscle weakness, loss of smell and taste current medication: none family history: has father with hypertension anthropometry and body composition: height: 175 cm weight: 83 kg bmi: 27.1 kg/m2 biochemical and hematological markers: blood pressure: 120/80 mmhg hemoglobin (hb): 13.5 g/dl white blood cells (wbc): 6,500 cells/mm³ platelet count: 200,000 cells/mm³ clinical: experienced severe respiratory symptoms during covid-19 currently in the recovery phase, grad

In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"

model_path = 'deepseek-ai/DeepSeek-R1-Distill-Llama-8B'

tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)



tokenizer_config.json:   0%|          | 0.00/3.07k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [ ]:
#Pass in a prompt and infer with the model
instruction = " folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. "

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/usr/local/lib/python3.11/dist-packages/bitsandbytes/nn/modules.py:451: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
 folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors:

In [ ]:
import re
model_modules = str(model.modules)
pattern = r'\((\w+)\): Linear'
linear_layer_names = re.findall(pattern, model_modules)

names = []
# Print the names of the Linear layers
for name in linear_layer_names:
    names.append(name)
target_modules = list(set(names))

In [ ]:
target_modules

['o_proj',
 'gate_proj',
 'up_proj',
 'down_proj',
 'v_proj',
 'lm_head',
 'q_proj',
 'k_proj']

In [ ]:
from peft import LoraConfig

#If only targeting attention blocks of the model
target_modules = ["q_proj", "v_proj"]

#If targeting all linear layers
target_modules = ['q_proj','k_proj','v_proj','o_proj','gate_proj','down_proj','up_proj','lm_head']

lora_config = LoraConfig(
r=16,
target_modules = target_modules,
lora_alpha=8,
lora_dropout=0.05,
bias="none",
task_type="CAUSAL_LM"
)

In [ ]:
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training

# Define training arguments
training_args=TrainingArguments(
    per_device_train_batch_size=2,  # Number of examples processed per device (GPU) at a time
    gradient_accumulation_steps=4,  # Accumulate gradients over 4 steps before updating weights
    num_train_epochs=1, # Full fine-tuning run
    warmup_steps=5,  # Gradually increases learning rate for the first 5 steps
    max_steps=45,  # Limits training to 60 steps (useful for debugging; increase for full fine-tuning)
    learning_rate=2e-4,  # Learning rate for weight updates (tuned for LoRA fine-tuning)
    logging_steps=5,  # Logs training progress every 10 steps
    optim="adamw_8bit",  # Uses memory-efficient AdamW optimizer in 8-bit mode
    weight_decay=0.01,  # Regularization to prevent overfitting
    lr_scheduler_type="linear",  # Uses a linear learning rate schedule
    seed=3407,  # Sets a fixed seed for reproducibility
    output_dir="outputs",  # Directory where fine-tuned model checkpoints will be saved
)

formatted_diet_df = diet_df[["formatted_prompt"]].copy()
formatted_diet_df = formatted_diet_df.rename(columns={"formatted_prompt": "text"})
dataset = Dataset.from_pandas(formatted_diet_df)
dataset_dict = DatasetDict({"train": dataset})


# Prepare for training by enabling input gradients and such
model = prepare_model_for_kbit_training(model)

# Attach LoRA adapters
model = get_peft_model(model, lora_config)
model.print_trainable_parameters()  # Optional: shows which params will be trained

trainer = SFTTrainer(
  model=model,
  train_dataset=dataset_dict["train"],  # Dataset used for training
  args=training_args,
)


trainable params: 44,060,672 || all params: 8,074,321,920 || trainable%: 0.5457


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Converting train dataset to ChatML:   0%|          | 0/50 [00:00<?, ? examples/s]

Applying chat template to train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

Tokenizing train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

Truncating train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [ ]:
# Start the fine-tuning process
trainer_stats = trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: mnithyashree-cs22 (chandanamn-cs23-na) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


In [ ]:
#Pass in a prompt and infer with the model
instruction = " for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy "

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


In [ ]:
model_name = "model_ft_diet"

# Save the fine-tuned model
model.save_pretrained(model_name)

# Save the tokenizer
tokenizer.save_pretrained(model_name)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


('model_ft_diet/tokenizer_config.json',
 'model_ft_diet/special_tokens_map.json',
 'model_ft_diet/tokenizer.json')

In [ ]:
from google.colab import files
import shutil

# Define the source directory of the model
model_dir = "model_ft_diet"

# Create a zip archive of the model directory
shutil.make_archive(model_dir, 'zip', model_dir)

# Download the zip file
files.download(f'{model_dir}.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Inference

In [ ]:
#Pass in a prompt and infer with the model
instruction = (
     "You are a health and diet tips generator. \n\n" +
    "Provide dietary recommendation for this patient profile: " +
" for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy "
)

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a health and diet tips generator. 

Provide dietary recommendation for this patient profile:  for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy 

### Response:

Recommendation: dietary recommendations for this patient with alcoholic neuropathy:  1. maintain a balanced diet with suf

In [ ]:
#Pass in a prompt and infer with the model
instruction = (
     "You are a health and diet tips generator. \n\n" +
    "Provide dietary recommendation for this patient profile: " +
" folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. "
)

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a health and diet tips generator. 

Provide dietary recommendation for this patient profile:  folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea

## One-day Diet Plan Fine-tuning

### Fine-tuning

In [ ]:
import torch # Import PyTorch
from trl import SFTTrainer # Trainer for supervised fine-tuning (SFT)
from huggingface_hub import login # Lets you login to API
from transformers import TrainingArguments # Defines training hyperparameters
from datasets import load_dataset # Lets you load fine-tuning datasets
import pandas as pd
from datasets import Dataset
import pandas as pd
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

In [ ]:
diet_df = pd.read_csv("patient_profiles_final.csv", names=["PatientProfile", "Recommendation", "DietPlan"], header=0)

In [ ]:
diet_df.shape

(50, 3)

In [ ]:
# Step 1: Create a combined instruction string
diet_df['instruction'] = (
    "You are a diet tips generator. \n\n" +
    "Given this patient profile: " + diet_df['PatientProfile'].astype(str) + "\n" +
    "Give a specific diet plan for the day (one-day diet plan) based on the patient profile using Central Asian food."
)

# Step 2: Combine both responses into a single response string
diet_df['response'] = (
    "One-day diet plan: " + diet_df['DietPlan'].astype(str) + "\n\n"
)


# Step 3: Define the prompt template
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}
"""

diet_df['formatted_prompt'] = diet_df.apply(
    lambda row: template.format(row['instruction'], row['response']),
    axis=1
)

In [ ]:
diet_df.shape

(50, 6)

In [ ]:
print(diet_df['formatted_prompt'].iloc[5])


Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a diet tips generator. 

Given this patient profile:  recovery after long covid name: erkinbek age: 42 gender: male ethnicity: kyrgyz location: taraz, kazakhstan marital status: married, has 4 children occupation: welder medical history: long covid-19 recovery date of covid-19 diagnosis: 8 months ago symptoms: persistent fatigue, shortness of breath, brain fog, muscle weakness, loss of smell and taste current medication: none family history: has father with hypertension anthropometry and body composition: height: 175 cm weight: 83 kg bmi: 27.1 kg/m2 biochemical and hematological markers: blood pressure: 120/80 mmhg hemoglobin (hb): 13.5 g/dl white blood cells (wbc): 6,500 cells/mm³ platelet count: 200,000 cells/mm³ clinical: experienced severe respiratory symptoms during covid-19 currently in the recovery phase, gradually improving diet during covid-19: br

In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"

model_path = 'deepseek-ai/DeepSeek-R1-Distill-Llama-8B'

tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)



tokenizer_config.json:   0%|          | 0.00/3.07k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [ ]:
#Pass in a prompt and infer with the model
instruction = " folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. "

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=256
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/usr/local/lib/python3.11/dist-packages/bitsandbytes/nn/modules.py:451: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
 folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors:

In [ ]:
import re
model_modules = str(model.modules)
pattern = r'\((\w+)\): Linear'
linear_layer_names = re.findall(pattern, model_modules)

names = []
# Print the names of the Linear layers
for name in linear_layer_names:
    names.append(name)
target_modules = list(set(names))

In [ ]:
target_modules

['lm_head',
 'v_proj',
 'gate_proj',
 'down_proj',
 'k_proj',
 'up_proj',
 'q_proj',
 'o_proj']

In [ ]:
from peft import LoraConfig

#If only targeting attention blocks of the model
target_modules = ["q_proj", "v_proj"]

#If targeting all linear layers
target_modules = ['q_proj','k_proj','v_proj','o_proj','gate_proj','down_proj','up_proj','lm_head']

lora_config = LoraConfig(
r=16,
target_modules = target_modules,
lora_alpha=8,
lora_dropout=0.05,
bias="none",
task_type="CAUSAL_LM"
)

In [ ]:
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training

# Define training arguments
training_args=TrainingArguments(
    per_device_train_batch_size=2,  # Number of examples processed per device (GPU) at a time
    gradient_accumulation_steps=4,  # Accumulate gradients over 4 steps before updating weights
    num_train_epochs=1, # Full fine-tuning run
    warmup_steps=5,  # Gradually increases learning rate for the first 5 steps
    max_steps=45,  # Limits training to 60 steps (useful for debugging; increase for full fine-tuning)
    learning_rate=2e-4,  # Learning rate for weight updates (tuned for LoRA fine-tuning)
    logging_steps=5,  # Logs training progress every 10 steps
    optim="adamw_8bit",  # Uses memory-efficient AdamW optimizer in 8-bit mode
    weight_decay=0.01,  # Regularization to prevent overfitting
    lr_scheduler_type="linear",  # Uses a linear learning rate schedule
    seed=3407,  # Sets a fixed seed for reproducibility
    output_dir="outputs",  # Directory where fine-tuned model checkpoints will be saved
)


formatted_diet_df = diet_df[["formatted_prompt"]].copy()
formatted_diet_df = formatted_diet_df.rename(columns={"formatted_prompt": "text"})
dataset = Dataset.from_pandas(formatted_diet_df)
dataset_dict = DatasetDict({"train": dataset})


# Prepare for training by enabling input gradients and such
model = prepare_model_for_kbit_training(model)

# Attach LoRA adapters
model = get_peft_model(model, lora_config)
model.print_trainable_parameters()  # Optional: shows which params will be trained

trainer = SFTTrainer(
  model=model,
  train_dataset=dataset_dict["train"],  # Dataset used for training
  args=training_args,
)


trainable params: 44,060,672 || all params: 8,074,321,920 || trainable%: 0.5457


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Converting train dataset to ChatML:   0%|          | 0/50 [00:00<?, ? examples/s]

Applying chat template to train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

Tokenizing train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

Truncating train dataset:   0%|          | 0/50 [00:00<?, ? examples/s]

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [ ]:
# Start the fine-tuning process
trainer_stats = trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: mnithyashree-cs22 (chandanamn-cs23-na) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


In [ ]:
#Pass in a prompt and infer with the model
instruction = (
    "You are a diet tips generator. \n\n" +
    "Given this patient profile: "  +
    " for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy " + "\n"
    "Give a specific diet plan for the day (one-day diet plan) based on the patient profile using Central Asian food."
)

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


In [ ]:
model_name = "model_ft_diet"

# Save the fine-tuned model
model.save_pretrained(model_name)

# Save the tokenizer
tokenizer.save_pretrained(model_name)


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


('model_ft_diet/tokenizer_config.json',
 'model_ft_diet/special_tokens_map.json',
 'model_ft_diet/tokenizer.json')

In [ ]:
from google.colab import files
import shutil

# Define the source directory of the model
model_dir = "model_ft_diet"

# Create a zip archive of the model directory
shutil.make_archive(model_dir, 'zip', model_dir)

# Download the zip file
files.download(f'{model_dir}.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Inference

In [ ]:
! unzip /content/model_ft_diet_separate_dietplan.zip

Archive:  /content/model_ft_diet_separate_dietplan.zip
  inflating: tokenizer_config.json   
  inflating: special_tokens_map.json  
  inflating: adapter_config.json     
  inflating: README.md               
  inflating: adapter_model.safetensors  
  inflating: tokenizer.json          


In [ ]:
import torch
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
from datasets import load_dataset, DatasetDict
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer
from peft import get_peft_model, LoraConfig, TaskType

device = "cuda" if torch.cuda.is_available() else "cpu"
model_path = 'deepseek-ai/DeepSeek-R1-Distill-Llama-8B'
tokenizer = AutoTokenizer.from_pretrained(model_path, token=hugging_face_token, load_in_4bit=True) # Load the model in 4-bit quantization to save memory)
model = AutoModelForCausalLM.from_pretrained(model_path, load_in_4bit=True, device_map="auto", token=hugging_face_token)


tokenizer_config.json:   0%|          | 0.00/3.07k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/826 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00001-of-000002.safetensors:   0%|          | 0.00/8.67G [00:00<?, ?B/s]

model-00002-of-000002.safetensors:   0%|          | 0.00/7.39G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel, PeftConfig

# Load the adapter config to find the base model
peft_model_path = "model_ft_diet_separate_dietplan"
config = PeftConfig.from_pretrained(peft_model_path)

# Load the model with the LoRA adapters
model = PeftModel.from_pretrained(model, peft_model_path)

# Set to eval mode
model.eval()


PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(128256, 4096)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
              (k_proj): lor

In [ ]:
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}
"""

#Pass in a prompt and infer with the model
instruction = (
    "You are a diet tips generator. \n\n" +
    "Given this patient profile: "  +
    " for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy " + "\n"
    "Give a specific diet plan for the day (one-day diet plan) based on the patient profile using Central Asian food."
)

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/usr/local/lib/python3.11/dist-packages/bitsandbytes/nn/modules.py:451: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a diet tips generator. 

Given this patient profile:  for this 45-year-old man with a history of alcohol use, presenting with sudden onset dysarthria, shuffling gait, and intention tremors, is likely alcoholic neuropathy. While alcoholism is known to cause neuropathy, the sudden onset of symptoms may also be related to other conditions such as vitamin deficiency, especially vitamin B12 deficiency, which can produce similar symptoms. However, given the history of alcohol use and the absence of other symptoms like numbness or tingling, alcoholic neuropathy is the more likely culprit. Therefore, the most probable diagnosis in this scenario is alcoholic neuropathy 
Give a specific diet plan for the day (one-day diet plan) based on the patient profile using Central Asian food.

### Response:

One-day diet plan:  breakfast: - 1 bowl of buckw

In [ ]:
template = """Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}
"""

#Pass in a prompt and infer with the model
instruction = (
    "You are a diet tips generator. \n\n" +
    "Given this patient profile: "  +
" folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, chak-chak, coke environmental, behavioral, and social factors: karima lives alone with her three children. karima sometimes works night shifts. karima's busy lifestyle includes taking her children to school and kindergarten, working at a local supermarket, cooking for her children, and doing chores. karima mentions not having time for regular exercise. additional information she has been in routine check up where she was diagnosed with folate deficiency anemia. she was referred to a hematologist who recommended dietary adjustments. karima, as a tatar, frequently consumes traditional cuisine that may not provide sufficient folate. to address her condition, she seeks guidance from a dietitian to incorporate folate-rich foods into her meals. " + "\n"
    "Give a specific diet plan for the day (one-day diet plan) based on the patient profile using Central Asian food."
)

prompt = template.format(instruction, "")
input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

generation_output = model.generate(
input_ids=input_ids, max_new_tokens=512
)

print(tokenizer.decode(generation_output[0]))

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


<｜begin▁of▁sentence｜>Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
You are a diet tips generator. 

Given this patient profile:  folate deficiency anemia name: karima age: 38 gender: female ethnicity: tatar location: atyrau, kazakhstan marital status: divorced occupation: salesman at a local supermarket medical history: diagnosis: folate deficiency anemia symptoms: weakness, fatigue past medical history: none provided family history: no information provided medication: none provided anthropometry, body composition, and functional assessment: height: 165 cm weight: 63 kg waist circumference: 80 cm biochemical and hematological markers: serum folate: 3.2 ng/ml serum iron: 65 mcg/dl serum vitamin b12: 400 pg/ml red blood cell count: 4.2 million cells/mcl mean corpuscular volume (mcv): 110 fl diet: typical foods consumed: white bread toast with butter and jam, coffee or tea, rice with chicken, plov, echpochmak, c